In [91]:
import folium
import pandas as pd
google_tile = folium.TileLayer(tiles = 'https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}', attr = 'Powered by Google', name='Google', overlay=False, control=False)
m = folium.Map(location=[7.94, 1.02], zoom_start=6, tiles=None)
google_tile.add_to(m);

In [92]:
regions = 'ghana_regions.geojson'
districts = 'ghana_districts.geojson'
df = pd.read_csv('gha_adminboundaries_tabulardata.csv')

#folium.GeoJson(regions, name="regions").add_to(m)
#folium.GeoJson(districts, name="districts").add_to(m)

cr = folium.Choropleth(
    geo_data=regions,
    name="regions",
    data=df,
    columns=["admin1Pcode", "region_value"],
    key_on="feature.properties.ADM1_PCODE",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="region_value",
    show=False
).add_to(m)

for s in cr.geojson.data['features']:
    region_code = s['properties']['ADM1_PCODE']
    s['properties']['region'] = s['properties']['ADM1_EN']
    s['properties']['region_value'] = float(df[df['admin1Pcode']==region_code]['region_value'].unique())

cr.geojson.add_child(
    folium.features.GeoJsonTooltip(['region', 'region_value'], labels=True)
)

cs = folium.Choropleth(
    geo_data=districts,
    name="districts",
    data=df,
    columns=["admin2Pcode", "district_value"],
    key_on="feature.properties.ADM2_PCODE",
    fill_color="PuBu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="district_value",
).add_to(m)

for s in cs.geojson.data['features']:
    district_code = s['properties']['ADM2_PCODE']
    s['properties']['district'] = s['properties']['ADM2_EN'] 
    s['properties']['district_value'] = round(df[df['admin2Pcode']==district_code]['district_value'].squeeze(),2)

cs.geojson.add_child(
    folium.features.GeoJsonTooltip(['district', 'district_value'], labels=True)
)


**Figure 1**
This is my first voila project.

In [133]:
import pandas as pd
hc = pd.read_csv('2020_health_facilities_ghana.csv')
hc.head(3)

Region          District          FacilityName           Type  \
0  Ashanti     Offinso North     A.M.E Zion Clinic         Clinic   
1  Ashanti  Bekwai Municipal     Abenkyiman Clinic         Clinic   
2  Ashanti      Adansi North  Aboabo Health Centre  Health Centre   

           Town   Ownership  Latitude  Longitude  
0      Afrancho        CHAG   7.40801   -1.96317  
1  Anwiankwanta     Private   6.46312   -1.58592  
2   Aboabo No 2  Government   6.22393   -1.34982

In [134]:
hc.shape

(3756, 8)

In [135]:
hc['Type'].unique()

array(['Clinic', 'Health Centre', 'Maternity Home', 'CHPS', 'Hospital',
       'District Hospital', 'Centre', 'RCH', 'Training Institution',
       'Municipal Health Directorate', 'Teaching Hospital',
       'Regional Hospital', 'CPHS', 'District Health Directorate',
       'Regional Health Directorate', 'Polyclinic', 'Municipal Hospital',
       'Municipal  Health Directorate', 'Metropolitan Hospital',
       'Metropolitan Health Directorate', 'DHD', 'Psychiatric Hospital',
       'Research Institution', 'Others', 'clinic'], dtype=object)

In [136]:
# let's exclude health care centers which perform special functions
exclusion_criteria = ['Maternity Home', 'RCH', 'Training Institution', 'Municipal Health Directorate', 'District Health Directorate',
'Regional Health Directorate', 'Municipal  Health Directorate', 'DHD', 'Psychiatric Hospital', 'Research Institution', 'Others']

In [137]:
hc = hc[~hc['Type'].isin(exclusion_criteria)]
hc.shape

(3008, 8)

In [138]:
# drop health centers without coordinates information 
hc = hc[~hc['Latitude'].isna() & ~hc['Longitude'].isna()]
hc.shape

(2985, 8)

In [139]:
from sklearn.model_selection import train_test_split

# we will aim for 5% (~150 centers), considering the stratification: 
hc = hc[hc['District'].map(hc['District'].value_counts()) >= 2] 
out_experiment, in_experiment = train_test_split(hc, test_size=0.15, random_state=42, stratify=hc[['Region', 'District']])
in_experiment = in_experiment[in_experiment['District'].map(in_experiment['District'].value_counts()) >= 3] # because of the 3 groups
in_experiment.shape

# we will split those in 3 groups
remain, control = train_test_split(in_experiment, test_size=0.33, random_state=42, stratify=in_experiment[['Region', 'District']])
treatment_2, treatment_1 = train_test_split(remain, test_size=0.5, random_state=42, stratify=remain[['Region', 'District']])


ValueError: Found input variables with inconsistent numbers of samples: [288, 2983]

In [101]:
groups = {'control': [control, 'lightgray'], 'treatment_1': [treatment_1, 'beige'], 'treatment_2': [treatment_2, 'purple']}
for i in groups.items():
    group = folium.FeatureGroup(name=f'{i[0]}') 
    i[1][0].apply(lambda row:folium.Marker(location=[row["Latitude"], row["Longitude"]], tooltip=row['FacilityName'], icon=folium.Icon(color=i[1][1], icon="plus", prefix='fa')).add_to(group), axis=1);
    group.add_to(m)
folium.LayerControl().add_to(m)
m